In [28]:
import pandas as pd
import numpy as np
import nltk
import string

from sklearn.feature_extraction.text import CountVectorizer
from gensim.models import KeyedVectors
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

In [2]:
artigo_treino = pd.read_csv(r"D:\Databases\Files\word2vec-treino.csv")
artigo_teste = pd.read_csv(r"D:\Databases\Files\word2vec-teste.csv")
modelo = KeyedVectors.load_word2vec_format(r'D:\Databases\Files\cbow_s300.txt')

In [3]:
display(artigo_treino.sample(5))


title  \
48544  Dilma deve pedir a Alckmin, assediado por grup...   
11903  Braskem começa a produzir borracha a partir de...   
81955  Contra terrorismo, EUA e potências admitem arm...   
73837  Novas linhas de crédito para veículos não comp...   
59688  Conheça George Martin, o '5º Beatle', em 7 mús...   

                                                    text        date  \
48544  Dilma Rousseff deve enviar em breve emissário ...  2015-08-12   
11903  A petroquímica Braskem anunciou nesta segunda-...  2015-11-24   
81955  Estados Unidos, Alemanha, França, China e Rúss...  2016-05-16   
73837  O ministro da Fazenda, Joaquim Levy, disse nes...  2015-08-19   
59688  O lendário produtor musical britânico George M...  2016-09-03   

        category    subcategory  \
48544    colunas  monicabergamo   
11903    mercado            NaN   
81955      mundo            NaN   
73837    mercado            NaN   
59688  ilustrada            NaN   

                                                    link  
48544  http://www1.folha.uol.com.br/colunas/monicaber...  
11903  http://www1.folha.uol.com.br/mercado/2015/11/1...  
81955  http://www1.folha.uol.com.br/mundo/2016/05/177...  
73837  http://www1.folha.uol.com.br/mercado/2015/08/1...  
59688  http://www1.folha.uol.com.br/ilustrada/2016/03...

In [4]:
modelo.get_vector('china')

array([-1.49033e-01,  1.26020e-01,  2.17628e-01,  1.82684e-01,
        1.65151e-01, -1.59660e-01, -2.34411e-01,  6.00570e-02,
        8.03680e-02,  2.87578e-01, -4.81100e-03, -5.68800e-02,
        2.15676e-01,  8.65540e-02,  1.25983e-01,  3.36157e-01,
       -1.83254e-01, -1.18499e-01,  1.13010e-02,  1.03814e-01,
        9.37640e-02,  2.90178e-01, -1.64395e-01, -1.13300e-02,
       -1.80676e-01, -1.15820e-02,  1.08728e-01,  1.65898e-01,
        9.37900e-02,  2.66767e-01, -1.29890e-02,  9.16030e-02,
        2.21292e-01, -1.36497e-01, -4.26350e-02, -1.30038e-01,
        2.17067e-01, -1.01963e-01, -3.70960e-02,  1.42155e-01,
        3.41109e-01,  2.46560e-01,  1.27458e-01,  5.72360e-02,
       -1.47962e-01, -1.60290e-02,  1.86533e-01,  7.71550e-02,
       -3.50024e-01, -4.06085e-01,  1.67131e-01, -4.75230e-02,
        5.13780e-02, -1.28224e-01,  1.06580e-02, -2.92652e-01,
        1.40540e-01, -4.57049e-01,  1.31094e-01,  2.03234e-01,
        2.94019e-01,  7.38370e-02,  1.11554e-01, -1.642

In [5]:
modelo.most_similar('camila')

[('priscila', 0.5719656348228455),
 ('juliana', 0.5567224621772766),
 ('adriana', 0.5159330368041992),
 ('márcia', 0.5055967569351196),
 ('cristiane', 0.49424827098846436),
 ('jéssica', 0.49114835262298584),
 ('fernanda', 0.49057748913764954),
 ('raquel', 0.4889867603778839),
 ('fabiana', 0.48833224177360535),
 ('valéria', 0.4853321611881256)]

In [6]:
modelo.most_similar(positive=["brasil", "argentina"])

[('chile', 0.6781662702560425),
 ('peru', 0.634803295135498),
 ('venezuela', 0.6273865699768066),
 ('equador', 0.6037014126777649),
 ('bolívia', 0.6017141342163086),
 ('haiti', 0.5993806719779968),
 ('méxico', 0.596230685710907),
 ('paraguai', 0.5957703590393066),
 ('uruguai', 0.590367317199707),
 ('japão', 0.5893509387969971)]

In [7]:
modelo.most_similar(positive=["nuvens", "estrela"], negative=['nuvem'])

[('estrelas', 0.5497430562973022),
 ('plêiades', 0.3791979253292084),
 ('colinas', 0.3746805489063263),
 ('trovoadas', 0.373703271150589),
 ('sombras', 0.37341946363449097),
 ('pombas', 0.3726757764816284),
 ('corredoras', 0.3640727400779724),
 ('cigarras', 0.36065396666526794),
 ('galáxias', 0.35754913091659546),
 ('luas', 0.3575345277786255)]

In [8]:
modelo.most_similar(positive=["professor", "mulher"], negative=['homem'])

[('professora', 0.6192208528518677),
 ('aluna', 0.5449554324150085),
 ('esposa', 0.4978230893611908),
 ('ex-aluna', 0.4884248673915863),
 ('namorada', 0.4737858772277832),
 ('enfermeira', 0.4728144407272339),
 ('filha', 0.467373788356781),
 ('irmã', 0.4584590792655945),
 ('ex-namorada', 0.45824769139289856),
 ('ex-professora', 0.45104706287384033)]

In [9]:
# CBOW - Continous Bag of Words
# Skip-Gram
def tokenizador(texto):
    lista_alfanumerico = list()
    texto = texto.lower()

    for token_valido in nltk.word_tokenize(texto):
        if token_valido in string.punctuation:
            continue
        lista_alfanumerico.append(token_valido)

    return lista_alfanumerico


In [10]:
tokenizador("Texto Exmplo, 1234")

['texto', 'exmplo', '1234']

In [11]:
def combinacao_vetores_por_soma(palavras_numeros):
    vetor_resultante = np.zeros(300)
    for pn in palavras_numeros:
        try:
            vetor_resultante += modelo.get_vector(pn)
        except KeyError as e:
            print(f"Key not found {palavras_numeros}")
    return vetor_resultante


In [12]:
comb = combinacao_vetores_por_soma(tokenizador("Texto 1"))
comb


Key not found ['texto', '1']


array([ 5.03359996e-02,  2.15844005e-01, -8.99100006e-02,  3.39899987e-01,
        4.27290015e-02,  3.87139991e-02,  4.02019992e-02,  2.03725994e-01,
        3.60199995e-02, -2.90690009e-02,  3.12569998e-02,  6.63449988e-02,
       -1.51703998e-01, -8.04930031e-02,  8.07970017e-02,  5.49050011e-02,
       -2.48120993e-01,  9.28120017e-02,  1.02821000e-01,  1.23888001e-01,
       -1.70099005e-01, -1.07051998e-01, -1.46831006e-01, -6.40729964e-02,
        1.89805001e-01, -1.40533000e-01, -1.21820003e-01,  9.12839994e-02,
       -4.23519984e-02,  1.64030001e-01,  1.63265005e-01, -1.55397996e-01,
       -3.76500003e-02, -1.26919998e-02,  6.84309974e-02,  1.71388000e-01,
        1.52168006e-01,  2.57512987e-01,  3.97850014e-02,  3.28593999e-01,
        2.22309995e-02,  1.12200005e-03,  1.84438005e-01,  4.06600013e-02,
       -1.59680005e-02,  1.88660007e-02,  1.87436998e-01,  1.31270006e-01,
       -3.12339999e-02,  8.15469995e-02,  1.65878996e-01,  7.43720010e-02,
       -2.46252000e-01,  

In [13]:
def matriz_vetores(textos):
    x = len(textos)
    y = 300
    matriz = np.zeros((x, y))

    for i in range(x):
        pn = tokenizador(textos.iloc[i])
        matriz[i] = combinacao_vetores_por_soma(pn)
    return matriz


In [14]:
matriz_vetores_treino = matriz_vetores(artigo_treino.title)
matriz_vetores_teste = matriz_vetores(artigo_teste.title)


Key not found ['macron', 'e', 'le', 'pen', 'vão', 'ao', '2º', 'turno', 'na', 'frança', 'em', 'revés', 'de', 'siglas', 'tradicionais']
Key not found ['após', 'queda', 'em', 'maio', 'a', 'atividade', 'econômica', 'sobe', '0,5', 'em', 'junho', 'diz', 'bc']
Key not found ["'spartacus", 'oferece', 'um', 'duplo', 'retrato', 'de', 'batalhas', 'perdidas']
Key not found ['sobe', 'para', '86', 'o', 'número', 'de', 'mortos', 'no', 'atentado', 'terrorista', 'em', 'nice', 'na', 'frança']
Key not found ['após', '33', 'anos', 'angeli', 'despede-se', 'das', 'tirinhas', 'diárias', 'na', "'ilustrada"]
Key not found ['após', '33', 'anos', 'angeli', 'despede-se', 'das', 'tirinhas', 'diárias', 'na', "'ilustrada"]
Key not found ['mortes', 'em', 'acidentes', 'de', 'trânsito', 'caem', '27', 'na', 'cidade', 'e', '20', 'no', 'estado', 'de', 'sp']
Key not found ['mortes', 'em', 'acidentes', 'de', 'trânsito', 'caem', '27', 'na', 'cidade', 'e', '20', 'no', 'estado', 'de', 'sp']
Key not found ['daniel', 'craig', 's

In [15]:
matriz_vetores_teste.shape

(20513, 300)

In [16]:
matriz_vetores_treino.shape

(90000, 300)

In [20]:
LR = LogisticRegression(max_iter=200)

In [21]:
LR.fit(matriz_vetores_treino, artigo_treino.category)


LogisticRegression(max_iter=200)

In [22]:
LR.n_iter_

array([114])

In [26]:
accuracy = LR.score(matriz_vetores_teste, artigo_teste.category)

In [25]:
accuracy

0.7948130453858528

In [27]:
artigo_teste.category.unique()

array(['colunas', 'esporte', 'mercado', 'cotidiano', 'mundo', 'ilustrada'],
      dtype=object)

In [30]:
label_prevista = LR.predict(matriz_vetores_teste)
CR = classification_report(artigo_teste.category, label_prevista)
print(CR)

              precision    recall  f1-score   support

     colunas       0.86      0.71      0.78      6103
   cotidiano       0.60      0.79      0.69      1698
     esporte       0.92      0.88      0.90      4663
   ilustrada       0.14      0.89      0.24       131
     mercado       0.84      0.79      0.81      5867
       mundo       0.74      0.85      0.79      2051

    accuracy                           0.79     20513
   macro avg       0.68      0.82      0.70     20513
weighted avg       0.83      0.79      0.81     20513

